# Language Translation
In this project, you’re going to take a peek into the realm of neural network machine translation.  You’ll be training a sequence to sequence model on a dataset of English and French sentences that can translate new sentences from English to French.
## Get the Data
Since translating the whole language of English to French will take lots of time to train, we have provided you with a small portion of the English corpus.

In [1]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import helper
import problem_unittests as tests

source_path = 'data/small_vocab_en'
target_path = 'data/small_vocab_fr'
source_text = helper.load_data(source_path)
target_text = helper.load_data(target_path)

## Explore the Data
Play around with view_sentence_range to view different parts of the data.

In [2]:
view_sentence_range = (11, 20)

"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import numpy as np

print('Dataset Stats')
print('Roughly the number of unique words: {}'.format(len({word: None for word in source_text.split()})))

sentences = source_text.split('\n')
word_counts = [len(sentence.split()) for sentence in sentences]
print('Number of sentences: {}'.format(len(sentences)))
print('Average number of words in a sentence: {}'.format(np.average(word_counts)))

print()
print('English sentences {} to {}:'.format(*view_sentence_range))
print('\n'.join(source_text.split('\n')[view_sentence_range[0]:view_sentence_range[1]]))
print()
print('French sentences {} to {}:'.format(*view_sentence_range))
print('\n'.join(target_text.split('\n')[view_sentence_range[0]:view_sentence_range[1]]))

Dataset Stats
Roughly the number of unique words: 227
Number of sentences: 137861
Average number of words in a sentence: 13.225277634719028

English sentences 11 to 20:
he saw a old yellow truck .
india is rainy during june , and it is sometimes warm in november .
that cat was my most loved animal .
he dislikes grapefruit , limes , and lemons .
her least liked fruit is the lemon , but his least liked is the grapefruit .
california is never cold during february , but it is sometimes freezing in june .
china is usually pleasant during autumn , and it is usually quiet in october .
paris is never freezing during november , but it is wonderful in october .
the united states is never rainy during january , but it is sometimes mild in october .

French sentences 11 to 20:
il a vu un vieux camion jaune .
inde est pluvieux en juin , et il est parfois chaud en novembre .
ce chat était mon animal le plus aimé .
il n'aime pamplemousse , citrons verts et les citrons .
son fruit est moins aimé le ci

## Implement Preprocessing Function
### Text to Word Ids
As you did with other RNNs, you must turn the text into a number so the computer can understand it. In the function `text_to_ids()`, you'll turn `source_text` and `target_text` from words to ids.  However, you need to add the `<EOS>` word id at the end of each sentence from `target_text`.  This will help the neural network predict when the sentence should end.

You can get the `<EOS>` word id by doing:
```python
target_vocab_to_int['<EOS>']
```
You can get other word ids using `source_vocab_to_int` and `target_vocab_to_int`.

In [3]:
def text_to_ids(source_text, target_text, source_vocab_to_int, target_vocab_to_int):
    """
    Convert source and target text to proper word ids
    :param source_text: String that contains all the source text.
    :param target_text: String that contains all the target text.
    :param source_vocab_to_int: Dictionary to go from the source words to an id
    :param target_vocab_to_int: Dictionary to go from the target words to an id
    :return: A tuple of lists (source_id_text, target_id_text)
    """
    # TODO: Implement Function
    source_word_ids = [[source_vocab_to_int.get(word, 0) for word in line.split()] for line in source_text.split('\n')]
    target_word_ids = [[target_vocab_to_int.get(word, 0) for word in line.split()] for line in target_text.split('\n')]
    length_source = len(source_word_ids)
    length_target = len(target_word_ids)
    length = min(length_source,length_target)
    source_id_text = []
    target_id_text = []
    for i in range(length):
        source_id_text.append(source_word_ids[i])
        target_id_text.append(target_word_ids[i] + [target_vocab_to_int['<EOS>']])


    return (source_id_text, target_id_text)

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_text_to_ids(text_to_ids)

Tests Passed


### Preprocess all the data and save it
Running the code cell below will preprocess all the data and save it to file.

In [4]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
helper.preprocess_and_save_data(source_path, target_path, text_to_ids)

# Check Point
This is your first checkpoint. If you ever decide to come back to this notebook or have to restart the notebook, you can start from here. The preprocessed data has been saved to disk.

In [5]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import numpy as np
import helper

(source_int_text, target_int_text), (source_vocab_to_int, target_vocab_to_int), _ = helper.load_preprocess()

### Check the Version of TensorFlow and Access to GPU
This will check to make sure you have the correct version of TensorFlow and access to a GPU

In [6]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
from distutils.version import LooseVersion
import warnings
import tensorflow as tf

# Check TensorFlow Version
assert LooseVersion(tf.__version__) >= LooseVersion('1.0'), 'Please use TensorFlow version 1.0 or newer'
print('TensorFlow Version: {}'.format(tf.__version__))

# Check for a GPU
if not tf.test.gpu_device_name():
    warnings.warn('No GPU found. Please use a GPU to train your neural network.')
else:
    print('Default GPU Device: {}'.format(tf.test.gpu_device_name()))

TensorFlow Version: 1.0.1


C:\Users\pc1\Anaconda3\envs\tensorflow\lib\site-packages\ipykernel\__main__.py:14: UserWarning: No GPU found. Please use a GPU to train your neural network.


## Build the Neural Network
You'll build the components necessary to build a Sequence-to-Sequence model by implementing the following functions below:
- `model_inputs`
- `process_decoding_input`
- `encoding_layer`
- `decoding_layer_train`
- `decoding_layer_infer`
- `decoding_layer`
- `seq2seq_model`

### Input
Implement the `model_inputs()` function to create TF Placeholders for the Neural Network. It should create the following placeholders:

- Input text placeholder named "input" using the TF Placeholder name parameter with rank 2.
- Targets placeholder with rank 2.
- Learning rate placeholder with rank 0.
- Keep probability placeholder named "keep_prob" using the TF Placeholder name parameter with rank 0.

Return the placeholders in the following the tuple (Input, Targets, Learing Rate, Keep Probability)

In [7]:
def model_inputs():
    """
    Create TF Placeholders for input, targets, and learning rate.
    :return: Tuple (input, targets, learning rate, keep probability)
    """
    # TODO: Implement Function
    input_data = tf.placeholder(tf.int32, [None, None] ,name='input')
    targets = tf.placeholder(tf.int32, [None, None])
    lr = tf.placeholder(tf.float32)
    keep_probability = tf.placeholder(tf.float32, name='keep_prob' )
    return input_data, targets, lr, keep_probability

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_model_inputs(model_inputs)

Tests Passed


### Process Decoding Input
Implement `process_decoding_input` using TensorFlow to remove the last word id from each batch in `target_data` and concat the GO ID to the begining of each batch.

In [8]:
def process_decoding_input(target_data, target_vocab_to_int, batch_size):
    """
    Preprocess target data for dencoding
    :param target_data: Target Placehoder
    :param target_vocab_to_int: Dictionary to go from the target words to an id
    :param batch_size: Batch Size
    :return: Preprocessed target data
    """
    # TODO: Implement Function
    
    
    ending = tf.strided_slice(target_data, [0, 0], [batch_size, -1], [1, 1])
    dec_input = tf.concat([tf.fill([batch_size, 1],target_vocab_to_int['<GO>']), ending], 1)
    
    
    return dec_input

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_process_decoding_input(process_decoding_input)

Tests Passed


### Encoding
Implement `encoding_layer()` to create a Encoder RNN layer using [`tf.nn.dynamic_rnn()`](https://www.tensorflow.org/api_docs/python/tf/nn/dynamic_rnn).

In [9]:
def encoding_layer(rnn_inputs, rnn_size, num_layers, keep_prob):
    """
    Create encoding layer
    :param rnn_inputs: Inputs for the RNN
    :param rnn_size: RNN Size
    :param num_layers: Number of layers
    :param keep_prob: Dropout keep probability
    :return: RNN state
    """
    # TODO: Implement Function
    # Source: https://discussions.udacity.com/t/encoding-layers/240119
    
    LSTM = tf.contrib.rnn.BasicLSTMCell(rnn_size)
    cell = tf.contrib.rnn.MultiRNNCell([LSTM]* num_layers)
    cell = tf.contrib.rnn.DropoutWrapper(cell, output_keep_prob=keep_prob)
    RNN_output, RNN_state = tf.nn.dynamic_rnn(cell, rnn_inputs, dtype=tf.float32)
    
    return RNN_state



"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_encoding_layer(encoding_layer)

Tests Passed


### Decoding - Training
Create training logits using [`tf.contrib.seq2seq.simple_decoder_fn_train()`](https://www.tensorflow.org/api_docs/python/tf/contrib/seq2seq/simple_decoder_fn_train) and [`tf.contrib.seq2seq.dynamic_rnn_decoder()`](https://www.tensorflow.org/api_docs/python/tf/contrib/seq2seq/dynamic_rnn_decoder).  Apply the `output_fn` to the [`tf.contrib.seq2seq.dynamic_rnn_decoder()`](https://www.tensorflow.org/api_docs/python/tf/contrib/seq2seq/dynamic_rnn_decoder) outputs.

In [10]:
def decoding_layer_train(encoder_state, dec_cell, dec_embed_input, sequence_length, decoding_scope,
                         output_fn, keep_prob):
    """
    Create a decoding layer for training
    :param encoder_state: Encoder State
    :param dec_cell: Decoder RNN Cell
    :param dec_embed_input: Decoder embedded input
    :param sequence_length: Sequence Length
    :param decoding_scope: TenorFlow Variable Scope for decoding
    :param output_fn: Function to apply the output layer
    :param keep_prob: Dropout keep probability
    :return: Train Logits
    """
    # TODO: Implement Function
    train_decoder_fn = tf.contrib.seq2seq.simple_decoder_fn_train(encoder_state)
    train_pred, _, _ = tf.contrib.seq2seq.dynamic_rnn_decoder(
        dec_cell, train_decoder_fn, dec_embed_input, sequence_length, scope=decoding_scope)
    train_pred= tf.contrib.layers.dropout(train_pred, keep_prob)
    train_logits =  output_fn(train_pred)
    return train_logits

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_decoding_layer_train(decoding_layer_train)

Tests Passed


### Decoding - Inference
Create inference logits using [`tf.contrib.seq2seq.simple_decoder_fn_inference()`](https://www.tensorflow.org/api_docs/python/tf/contrib/seq2seq/simple_decoder_fn_inference) and [`tf.contrib.seq2seq.dynamic_rnn_decoder()`](https://www.tensorflow.org/api_docs/python/tf/contrib/seq2seq/dynamic_rnn_decoder). 

In [11]:
def decoding_layer_infer(encoder_state, dec_cell, dec_embeddings, start_of_sequence_id, end_of_sequence_id,
                         maximum_length, vocab_size, decoding_scope, output_fn, keep_prob):
    """
    Create a decoding layer for inference
    :param encoder_state: Encoder state
    :param dec_cell: Decoder RNN Cell
    :param dec_embeddings: Decoder embeddings
    :param start_of_sequence_id: GO ID
    :param end_of_sequence_id: EOS Id
    :param maximum_length: Maximum length of 
    :param vocab_size: Size of vocabulary
    :param decoding_scope: TensorFlow Variable Scope for decoding
    :param output_fn: Function to apply the output layer
    :param keep_prob: Dropout keep probability
    :return: Inference Logits
    """
    # TODO: Implement Function
    infer_decoder_fn = tf.contrib.seq2seq.simple_decoder_fn_inference(
        output_fn, encoder_state, dec_embeddings, start_of_sequence_id, end_of_sequence_id, 
        maximum_length - 1, vocab_size)
    inference_logits, _, _ = tf.contrib.seq2seq.dynamic_rnn_decoder(dec_cell, infer_decoder_fn, scope=decoding_scope)
    #inference_logits= tf.nn.dropout(inference_logits, keep_prob)    
    inference_logits= tf.contrib.layers.dropout(inference_logits, keep_prob)  
    return inference_logits


"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_decoding_layer_infer(decoding_layer_infer)

Tests Passed


### Build the Decoding Layer
Implement `decoding_layer()` to create a Decoder RNN layer.

- Create RNN cell for decoding using `rnn_size` and `num_layers`.
- Create the output fuction using [`lambda`](https://docs.python.org/3/tutorial/controlflow.html#lambda-expressions) to transform it's input, logits, to class logits.
- Use the your `decoding_layer_train(encoder_state, dec_cell, dec_embed_input, sequence_length, decoding_scope, output_fn, keep_prob)` function to get the training logits.
- Use your `decoding_layer_infer(encoder_state, dec_cell, dec_embeddings, start_of_sequence_id, end_of_sequence_id, maximum_length, vocab_size, decoding_scope, output_fn, keep_prob)` function to get the inference logits.

Note: You'll need to use [tf.variable_scope](https://www.tensorflow.org/api_docs/python/tf/variable_scope) to share variables between training and inference.

In [12]:
def decoding_layer(dec_embed_input, dec_embeddings, encoder_state, vocab_size, sequence_length, rnn_size,
                   num_layers, target_vocab_to_int, keep_prob):
    """
    Create decoding layer
    :param dec_embed_input: Decoder embedded input
    :param dec_embeddings: Decoder embeddings
    :param encoder_state: The encoded state
    :param vocab_size: Size of vocabulary
    :param sequence_length: Sequence Length
    :param rnn_size: RNN Size
    :param num_layers: Number of layers
    :param target_vocab_to_int: Dictionary to go from the target words to an id
    :param keep_prob: Dropout keep probability
    :return: Tuple of (Training Logits, Inference Logits)
    """
    # TODO: Implement Function
    
    LSTM = tf.contrib.rnn.BasicLSTMCell(rnn_size)
    dec_cell = tf.contrib.rnn.DropoutWrapper(LSTM, output_keep_prob=keep_prob)
    dec_cell = tf.contrib.rnn.MultiRNNCell([dec_cell]*num_layers)
    
    with tf.variable_scope("decoding") as decoding_scope:
        output_fn = lambda x: tf.contrib.layers.fully_connected(x, vocab_size, None, scope=decoding_scope)
    
    with tf.variable_scope('decoding') as decoding_scope:
        train_logits = decoding_layer_train(encoder_state, dec_cell, dec_embed_input, sequence_length, 
                                            decoding_scope, output_fn, keep_prob)
    
    with tf.variable_scope('decoding', reuse=True) as infer_scope:
        inference_logits = decoding_layer_infer(encoder_state, dec_cell, dec_embeddings, target_vocab_to_int['<GO>'],
                                           target_vocab_to_int['<EOS>'], sequence_length, vocab_size, infer_scope,
                                           output_fn, keep_prob)

    return (train_logits, inference_logits)




"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_decoding_layer(decoding_layer)

Tests Passed


### Build the Neural Network
Apply the functions you implemented above to:

- Apply embedding to the input data for the encoder.
- Encode the input using your `encoding_layer(rnn_inputs, rnn_size, num_layers, keep_prob)`.
- Process target data using your `process_decoding_input(target_data, target_vocab_to_int, batch_size)` function.
- Apply embedding to the target data for the decoder.
- Decode the encoded input using your `decoding_layer(dec_embed_input, dec_embeddings, encoder_state, vocab_size, sequence_length, rnn_size, num_layers, target_vocab_to_int, keep_prob)`.

In [13]:
def seq2seq_model(input_data, target_data, keep_prob, batch_size, sequence_length, source_vocab_size, target_vocab_size,
                  enc_embedding_size, dec_embedding_size, rnn_size, num_layers, target_vocab_to_int):
    """
    Build the Sequence-to-Sequence part of the neural network
    :param input_data: Input placeholder
    :param target_data: Target placeholder
    :param keep_prob: Dropout keep probability placeholder
    :param batch_size: Batch Size
    :param sequence_length: Sequence Length
    :param source_vocab_size: Source vocabulary size
    :param target_vocab_size: Target vocabulary size
    :param enc_embedding_size: Decoder embedding size
    :param dec_embedding_size: Encoder embedding size
    :param rnn_size: RNN Size
    :param num_layers: Number of layers
    :param target_vocab_to_int: Dictionary to go from the target words to an id
    :return: Tuple of (Training Logits, Inference Logits)
    """
    # TODO: Implement Function
    # Encoder embedding
    enc_embed_input = tf.contrib.layers.embed_sequence(input_data, source_vocab_size, enc_embedding_size)
    encoder_state = encoding_layer(enc_embed_input, rnn_size, num_layers, keep_prob)

    dec_input = process_decoding_input(target_data, target_vocab_to_int, batch_size)
    dec_embeddings = tf.Variable(tf.random_uniform([target_vocab_size, dec_embedding_size]))
    dec_embed_input = tf.nn.embedding_lookup(dec_embeddings, dec_input)
    
    training_logits, inference_logits = decoding_layer(dec_embed_input, dec_embeddings, encoder_state, target_vocab_size, sequence_length, rnn_size,
                                                       num_layers, target_vocab_to_int, keep_prob)

    return (training_logits, inference_logits)

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_seq2seq_model(seq2seq_model)

Tests Passed


## Neural Network Training
### Hyperparameters
Tune the following parameters:

- Set `epochs` to the number of epochs.
- Set `batch_size` to the batch size.
- Set `rnn_size` to the size of the RNNs.
- Set `num_layers` to the number of layers.
- Set `encoding_embedding_size` to the size of the embedding for the encoder.
- Set `decoding_embedding_size` to the size of the embedding for the decoder.
- Set `learning_rate` to the learning rate.
- Set `keep_probability` to the Dropout keep probability

In [14]:
# Number of Epochs
epochs = 80
# Batch Size
batch_size = 256
# RNN Size
rnn_size = 100
# Number of Layers
num_layers = 3
# Embedding Size
encoding_embedding_size = 50
decoding_embedding_size = 50
# Learning Rate
learning_rate = 0.001
# Dropout Keep Probability
keep_probability = 0.7

### Build the Graph
Build the graph using the neural network you implemented.

In [15]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
save_path = 'checkpoints/dev'
(source_int_text, target_int_text), (source_vocab_to_int, target_vocab_to_int), _ = helper.load_preprocess()
max_target_sentence_length = max([len(sentence) for sentence in source_int_text])

train_graph = tf.Graph()
with train_graph.as_default():
    input_data, targets, lr, keep_prob = model_inputs()
    sequence_length = tf.placeholder_with_default(max_target_sentence_length, None, name='sequence_length')
    input_shape = tf.shape(input_data)
    
    train_logits, inference_logits = seq2seq_model(
        tf.reverse(input_data, [-1]), targets, keep_prob, batch_size, sequence_length, len(source_vocab_to_int), len(target_vocab_to_int),
        encoding_embedding_size, decoding_embedding_size, rnn_size, num_layers, target_vocab_to_int)

    tf.identity(inference_logits, 'logits')
    with tf.name_scope("optimization"):
        # Loss function
        cost = tf.contrib.seq2seq.sequence_loss(
            train_logits,
            targets,
            tf.ones([input_shape[0], sequence_length]))

        # Optimizer
        optimizer = tf.train.AdamOptimizer(lr)

        # Gradient Clipping
        gradients = optimizer.compute_gradients(cost)
        capped_gradients = [(tf.clip_by_value(grad, -1., 1.), var) for grad, var in gradients if grad is not None]
        train_op = optimizer.apply_gradients(capped_gradients)

### Train
Train the neural network on the preprocessed data. If you have a hard time getting a good loss, check the forms to see if anyone is having the same problem.

In [16]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import time

def get_accuracy(target, logits):
    """
    Calculate accuracy
    """
    max_seq = max(target.shape[1], logits.shape[1])
    if max_seq - target.shape[1]:
        target = np.pad(
            target_batch,
            [(0,0),(0,max_seq - target_batch.shape[1]), (0,0)],
            'constant')
    if max_seq - batch_train_logits.shape[1]:
        logits = np.pad(
            logits,
            [(0,0),(0,max_seq - logits.shape[1]), (0,0)],
            'constant')

    return np.mean(np.equal(target, np.argmax(logits, 2)))

train_source = source_int_text[batch_size:]
train_target = target_int_text[batch_size:]

valid_source = helper.pad_sentence_batch(source_int_text[:batch_size])
valid_target = helper.pad_sentence_batch(target_int_text[:batch_size])

with tf.Session(graph=train_graph) as sess:
    sess.run(tf.global_variables_initializer())

    for epoch_i in range(epochs):
        for batch_i, (source_batch, target_batch) in enumerate(
                helper.batch_data(train_source, train_target, batch_size)):
            start_time = time.time()
            
            _, loss = sess.run(
                [train_op, cost],
                {input_data: source_batch,
                 targets: target_batch,
                 lr: learning_rate,
                 sequence_length: target_batch.shape[1],
                 keep_prob: keep_probability})
            
            batch_train_logits = sess.run(
                inference_logits,
                {input_data: source_batch, keep_prob: 1.0})
            batch_valid_logits = sess.run(
                inference_logits,
                {input_data: valid_source, keep_prob: 1.0})
                
            train_acc = get_accuracy(target_batch, batch_train_logits)
            valid_acc = get_accuracy(np.array(valid_target), batch_valid_logits)
            end_time = time.time()
            print('Epoch {:>3} Batch {:>4}/{} - Train Accuracy: {:>6.3f}, Validation Accuracy: {:>6.3f}, Loss: {:>6.3f}'
                  .format(epoch_i, batch_i, len(source_int_text) // batch_size, train_acc, valid_acc, loss))

    # Save Model
    saver = tf.train.Saver()
    saver.save(sess, save_path)
    print('Model Trained and Saved')

Epoch   0 Batch    0/538 - Train Accuracy:  0.234, Validation Accuracy:  0.316, Loss:  5.884
Epoch   0 Batch    1/538 - Train Accuracy:  0.235, Validation Accuracy:  0.318, Loss:  5.815
Epoch   0 Batch    2/538 - Train Accuracy:  0.255, Validation Accuracy:  0.319, Loss:  5.727
Epoch   0 Batch    3/538 - Train Accuracy:  0.234, Validation Accuracy:  0.320, Loss:  5.632
Epoch   0 Batch    4/538 - Train Accuracy:  0.246, Validation Accuracy:  0.322, Loss:  5.490
Epoch   0 Batch    5/538 - Train Accuracy:  0.269, Validation Accuracy:  0.322, Loss:  5.283
Epoch   0 Batch    6/538 - Train Accuracy:  0.276, Validation Accuracy:  0.322, Loss:  5.099
Epoch   0 Batch    7/538 - Train Accuracy:  0.253, Validation Accuracy:  0.322, Loss:  5.020
Epoch   0 Batch    8/538 - Train Accuracy:  0.250, Validation Accuracy:  0.322, Loss:  4.904
Epoch   0 Batch    9/538 - Train Accuracy:  0.251, Validation Accuracy:  0.322, Loss:  4.799
Epoch   0 Batch   10/538 - Train Accuracy:  0.229, Validation Accuracy

Epoch   0 Batch   89/538 - Train Accuracy:  0.371, Validation Accuracy:  0.428, Loss:  2.916
Epoch   0 Batch   90/538 - Train Accuracy:  0.407, Validation Accuracy:  0.442, Loss:  2.821
Epoch   0 Batch   91/538 - Train Accuracy:  0.371, Validation Accuracy:  0.440, Loss:  2.954
Epoch   0 Batch   92/538 - Train Accuracy:  0.378, Validation Accuracy:  0.436, Loss:  2.896
Epoch   0 Batch   93/538 - Train Accuracy:  0.370, Validation Accuracy:  0.442, Loss:  2.931
Epoch   0 Batch   94/538 - Train Accuracy:  0.371, Validation Accuracy:  0.440, Loss:  2.953
Epoch   0 Batch   95/538 - Train Accuracy:  0.431, Validation Accuracy:  0.443, Loss:  2.665
Epoch   0 Batch   96/538 - Train Accuracy:  0.417, Validation Accuracy:  0.444, Loss:  2.733
Epoch   0 Batch   97/538 - Train Accuracy:  0.379, Validation Accuracy:  0.447, Loss:  2.896
Epoch   0 Batch   98/538 - Train Accuracy:  0.415, Validation Accuracy:  0.444, Loss:  2.695
Epoch   0 Batch   99/538 - Train Accuracy:  0.382, Validation Accuracy

Epoch   0 Batch  178/538 - Train Accuracy:  0.465, Validation Accuracy:  0.485, Loss:  2.297
Epoch   0 Batch  179/538 - Train Accuracy:  0.449, Validation Accuracy:  0.501, Loss:  2.447
Epoch   0 Batch  180/538 - Train Accuracy:  0.479, Validation Accuracy:  0.498, Loss:  2.339
Epoch   0 Batch  181/538 - Train Accuracy:  0.408, Validation Accuracy:  0.486, Loss:  2.472
Epoch   0 Batch  182/538 - Train Accuracy:  0.429, Validation Accuracy:  0.495, Loss:  2.489
Epoch   0 Batch  183/538 - Train Accuracy:  0.467, Validation Accuracy:  0.497, Loss:  2.341
Epoch   0 Batch  184/538 - Train Accuracy:  0.437, Validation Accuracy:  0.478, Loss:  2.323
Epoch   0 Batch  185/538 - Train Accuracy:  0.444, Validation Accuracy:  0.493, Loss:  2.385
Epoch   0 Batch  186/538 - Train Accuracy:  0.460, Validation Accuracy:  0.503, Loss:  2.340
Epoch   0 Batch  187/538 - Train Accuracy:  0.479, Validation Accuracy:  0.491, Loss:  2.257
Epoch   0 Batch  188/538 - Train Accuracy:  0.410, Validation Accuracy

Epoch   0 Batch  267/538 - Train Accuracy:  0.434, Validation Accuracy:  0.499, Loss:  2.185
Epoch   0 Batch  268/538 - Train Accuracy:  0.460, Validation Accuracy:  0.501, Loss:  2.093
Epoch   0 Batch  269/538 - Train Accuracy:  0.438, Validation Accuracy:  0.498, Loss:  2.136
Epoch   0 Batch  270/538 - Train Accuracy:  0.428, Validation Accuracy:  0.496, Loss:  2.191
Epoch   0 Batch  271/538 - Train Accuracy:  0.455, Validation Accuracy:  0.498, Loss:  2.196
Epoch   0 Batch  272/538 - Train Accuracy:  0.423, Validation Accuracy:  0.500, Loss:  2.263
Epoch   0 Batch  273/538 - Train Accuracy:  0.437, Validation Accuracy:  0.490, Loss:  2.151
Epoch   0 Batch  274/538 - Train Accuracy:  0.425, Validation Accuracy:  0.504, Loss:  2.239
Epoch   0 Batch  275/538 - Train Accuracy:  0.444, Validation Accuracy:  0.499, Loss:  2.178
Epoch   0 Batch  276/538 - Train Accuracy:  0.441, Validation Accuracy:  0.496, Loss:  2.172
Epoch   0 Batch  277/538 - Train Accuracy:  0.458, Validation Accuracy

Epoch   0 Batch  356/538 - Train Accuracy:  0.487, Validation Accuracy:  0.500, Loss:  1.830
Epoch   0 Batch  357/538 - Train Accuracy:  0.436, Validation Accuracy:  0.491, Loss:  1.974
Epoch   0 Batch  358/538 - Train Accuracy:  0.453, Validation Accuracy:  0.498, Loss:  1.971
Epoch   0 Batch  359/538 - Train Accuracy:  0.468, Validation Accuracy:  0.501, Loss:  1.877
Epoch   0 Batch  360/538 - Train Accuracy:  0.445, Validation Accuracy:  0.494, Loss:  1.978
Epoch   0 Batch  361/538 - Train Accuracy:  0.477, Validation Accuracy:  0.505, Loss:  1.888
Epoch   0 Batch  362/538 - Train Accuracy:  0.471, Validation Accuracy:  0.497, Loss:  1.817
Epoch   0 Batch  363/538 - Train Accuracy:  0.480, Validation Accuracy:  0.501, Loss:  1.843
Epoch   0 Batch  364/538 - Train Accuracy:  0.439, Validation Accuracy:  0.508, Loss:  1.959
Epoch   0 Batch  365/538 - Train Accuracy:  0.475, Validation Accuracy:  0.511, Loss:  1.900
Epoch   0 Batch  366/538 - Train Accuracy:  0.455, Validation Accuracy

...

Epoch  79 Batch  119/538 - Train Accuracy:  0.984, Validation Accuracy:  0.970, Loss:  0.011
Epoch  79 Batch  120/538 - Train Accuracy:  0.976, Validation Accuracy:  0.970, Loss:  0.015
Epoch  79 Batch  121/538 - Train Accuracy:  0.971, Validation Accuracy:  0.972, Loss:  0.021
Epoch  79 Batch  122/538 - Train Accuracy:  0.972, Validation Accuracy:  0.974, Loss:  0.012
Epoch  79 Batch  123/538 - Train Accuracy:  0.976, Validation Accuracy:  0.974, Loss:  0.013
Epoch  79 Batch  124/538 - Train Accuracy:  0.979, Validation Accuracy:  0.972, Loss:  0.013
Epoch  79 Batch  125/538 - Train Accuracy:  0.978, Validation Accuracy:  0.971, Loss:  0.017
Epoch  79 Batch  126/538 - Train Accuracy:  0.974, Validation Accuracy:  0.971, Loss:  0.019
Epoch  79 Batch  127/538 - Train Accuracy:  0.972, Validation Accuracy:  0.970, Loss:  0.017
Epoch  79 Batch  128/538 - Train Accuracy:  0.978, Validation Accuracy:  0.970, Loss:  0.015
Epoch  79 Batch  129/538 - Train Accuracy:  0.983, Validation Accuracy

Epoch  79 Batch  208/538 - Train Accuracy:  0.979, Validation Accuracy:  0.971, Loss:  0.028
Epoch  79 Batch  209/538 - Train Accuracy:  0.977, Validation Accuracy:  0.970, Loss:  0.018
Epoch  79 Batch  210/538 - Train Accuracy:  0.978, Validation Accuracy:  0.969, Loss:  0.017
Epoch  79 Batch  211/538 - Train Accuracy:  0.971, Validation Accuracy:  0.973, Loss:  0.015
Epoch  79 Batch  212/538 - Train Accuracy:  0.983, Validation Accuracy:  0.971, Loss:  0.011
Epoch  79 Batch  213/538 - Train Accuracy:  0.975, Validation Accuracy:  0.971, Loss:  0.017
Epoch  79 Batch  214/538 - Train Accuracy:  0.976, Validation Accuracy:  0.971, Loss:  0.011
Epoch  79 Batch  215/538 - Train Accuracy:  0.971, Validation Accuracy:  0.971, Loss:  0.014
Epoch  79 Batch  216/538 - Train Accuracy:  0.971, Validation Accuracy:  0.966, Loss:  0.020
Epoch  79 Batch  217/538 - Train Accuracy:  0.975, Validation Accuracy:  0.966, Loss:  0.019
Epoch  79 Batch  218/538 - Train Accuracy:  0.981, Validation Accuracy

Epoch  79 Batch  297/538 - Train Accuracy:  0.982, Validation Accuracy:  0.978, Loss:  0.015
Epoch  79 Batch  298/538 - Train Accuracy:  0.980, Validation Accuracy:  0.978, Loss:  0.012
Epoch  79 Batch  299/538 - Train Accuracy:  0.979, Validation Accuracy:  0.978, Loss:  0.017
Epoch  79 Batch  300/538 - Train Accuracy:  0.984, Validation Accuracy:  0.978, Loss:  0.013
Epoch  79 Batch  301/538 - Train Accuracy:  0.975, Validation Accuracy:  0.978, Loss:  0.022
Epoch  79 Batch  302/538 - Train Accuracy:  0.980, Validation Accuracy:  0.978, Loss:  0.019
Epoch  79 Batch  303/538 - Train Accuracy:  0.979, Validation Accuracy:  0.975, Loss:  0.020
Epoch  79 Batch  304/538 - Train Accuracy:  0.979, Validation Accuracy:  0.973, Loss:  0.016
Epoch  79 Batch  305/538 - Train Accuracy:  0.977, Validation Accuracy:  0.971, Loss:  0.014
Epoch  79 Batch  306/538 - Train Accuracy:  0.979, Validation Accuracy:  0.971, Loss:  0.017
Epoch  79 Batch  307/538 - Train Accuracy:  0.982, Validation Accuracy

Epoch  79 Batch  386/538 - Train Accuracy:  0.981, Validation Accuracy:  0.976, Loss:  0.017
Epoch  79 Batch  387/538 - Train Accuracy:  0.979, Validation Accuracy:  0.976, Loss:  0.017
Epoch  79 Batch  388/538 - Train Accuracy:  0.977, Validation Accuracy:  0.977, Loss:  0.014
Epoch  79 Batch  389/538 - Train Accuracy:  0.973, Validation Accuracy:  0.977, Loss:  0.014
Epoch  79 Batch  390/538 - Train Accuracy:  0.981, Validation Accuracy:  0.977, Loss:  0.008
Epoch  79 Batch  391/538 - Train Accuracy:  0.975, Validation Accuracy:  0.972, Loss:  0.014
Epoch  79 Batch  392/538 - Train Accuracy:  0.974, Validation Accuracy:  0.967, Loss:  0.014
Epoch  79 Batch  393/538 - Train Accuracy:  0.983, Validation Accuracy:  0.969, Loss:  0.015
Epoch  79 Batch  394/538 - Train Accuracy:  0.970, Validation Accuracy:  0.971, Loss:  0.015
Epoch  79 Batch  395/538 - Train Accuracy:  0.977, Validation Accuracy:  0.966, Loss:  0.018
Epoch  79 Batch  396/538 - Train Accuracy:  0.977, Validation Accuracy

Epoch  79 Batch  475/538 - Train Accuracy:  0.978, Validation Accuracy:  0.967, Loss:  0.013
Epoch  79 Batch  476/538 - Train Accuracy:  0.978, Validation Accuracy:  0.967, Loss:  0.015
Epoch  79 Batch  477/538 - Train Accuracy:  0.977, Validation Accuracy:  0.967, Loss:  0.020
Epoch  79 Batch  478/538 - Train Accuracy:  0.984, Validation Accuracy:  0.967, Loss:  0.011
Epoch  79 Batch  479/538 - Train Accuracy:  0.974, Validation Accuracy:  0.965, Loss:  0.014
Epoch  79 Batch  480/538 - Train Accuracy:  0.977, Validation Accuracy:  0.967, Loss:  0.016
Epoch  79 Batch  481/538 - Train Accuracy:  0.987, Validation Accuracy:  0.962, Loss:  0.016
Epoch  79 Batch  482/538 - Train Accuracy:  0.974, Validation Accuracy:  0.962, Loss:  0.011
Epoch  79 Batch  483/538 - Train Accuracy:  0.963, Validation Accuracy:  0.964, Loss:  0.018
Epoch  79 Batch  484/538 - Train Accuracy:  0.964, Validation Accuracy:  0.962, Loss:  0.015
Epoch  79 Batch  485/538 - Train Accuracy:  0.977, Validation Accuracy

### Save Parameters
Save the `batch_size` and `save_path` parameters for inference.

In [17]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
# Save parameters for checkpoint
helper.save_params(save_path)

# Checkpoint

In [18]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import tensorflow as tf
import numpy as np
import helper
import problem_unittests as tests

_, (source_vocab_to_int, target_vocab_to_int), (source_int_to_vocab, target_int_to_vocab) = helper.load_preprocess()
load_path = helper.load_params()

## Sentence to Sequence
To feed a sentence into the model for translation, you first need to preprocess it.  Implement the function `sentence_to_seq()` to preprocess new sentences.

- Convert the sentence to lowercase
- Convert words into ids using `vocab_to_int`
 - Convert words not in the vocabulary, to the `<UNK>` word id.

In [19]:
def sentence_to_seq(sentence, vocab_to_int):
    """
    Convert a sentence to a sequence of ids
    :param sentence: String
    :param vocab_to_int: Dictionary to go from the words to an id
    :return: List of word ids
    """
    # TODO: Implement Function
    unknow_id = vocab_to_int.get('<UNK>')
    word_id = [vocab_to_int.get(word,unknow_id) for word in sentence.lower().split()]

    return word_id

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_sentence_to_seq(sentence_to_seq)

Tests Passed


## Translate
This will translate `translate_sentence` from English to French.

In [20]:
translate_sentence = 'he saw a old yellow truck .'


"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
translate_sentence = sentence_to_seq(translate_sentence, source_vocab_to_int)

loaded_graph = tf.Graph()
with tf.Session(graph=loaded_graph) as sess:
    # Load saved model
    loader = tf.train.import_meta_graph(load_path + '.meta')
    loader.restore(sess, load_path)

    input_data = loaded_graph.get_tensor_by_name('input:0')
    logits = loaded_graph.get_tensor_by_name('logits:0')
    keep_prob = loaded_graph.get_tensor_by_name('keep_prob:0')

    translate_logits = sess.run(logits, {input_data: [translate_sentence], keep_prob: 1.0})[0]

print('Input')
print('  Word Ids:      {}'.format([i for i in translate_sentence]))
print('  English Words: {}'.format([source_int_to_vocab[i] for i in translate_sentence]))

print('\nPrediction')
print('  Word Ids:      {}'.format([i for i in np.argmax(translate_logits, 1)]))
print('  French Words: {}'.format([target_int_to_vocab[i] for i in np.argmax(translate_logits, 1)]))

Input
  Word Ids:      [230, 157, 227, 48, 205, 204, 17]
  English Words: ['he', 'saw', 'a', 'old', 'yellow', 'truck', '.']

Prediction
  Word Ids:      [262, 23, 181, 129, 277, 273, 1]
  French Words: ['il', "n'aime", 'un', 'vieux', 'camion', '.', '<EOS>']


## Imperfect Translation
You might notice that some sentences translate better than others.  Since the dataset you're using only has a vocabulary of 227 English words of the thousands that you use, you're only going to see good results using these words.  For this project, you don't need a perfect translation. However, if you want to create a better translation model, you'll need better data.

You can train on the [WMT10 French-English corpus](http://www.statmt.org/wmt10/training-giga-fren.tar).  This dataset has more vocabulary and richer in topics discussed.  However, this will take you days to train, so make sure you've a GPU and the neural network is performing well on dataset we provided.  Just make sure you play with the WMT10 corpus after you've submitted this project.
## Submitting This Project
When submitting this project, make sure to run all the cells before saving the notebook. Save the notebook file as "dlnd_language_translation.ipynb" and save it as a HTML file under "File" -> "Download as". Include the "helper.py" and "problem_unittests.py" files in your submission.